In [3]:
import pandas as pd
import folium


In [5]:
!ls data

girond.csv


In [8]:
pd.read_csv("data/girond.csv").to_pickle("full.pkl")

In [9]:
!open .

In [13]:
def get_data(path="data/girond.csv"):
    data = pd.read_csv(path)
    #print(data.columns)
    data = data[["date_mutation","nature_mutation","nom_commune","valeur_fonciere","adresse_nom_voie","surface_reelle_bati", "type_local",'longitude', 'latitude']]
    return data

In [78]:
def get_data_selected(data, nom_commune = "Bordeaux",
                      type_local = "Maison",
                      nature_mutation = "Vente"):
    
    data = data[data["nom_commune"] == nom_commune]
    data = data[data["type_local"] == type_local]
    data = data[data["nature_mutation"] == nature_mutation]

    data = data.dropna(subset=["longitude","latitude", "surface_reelle_bati"])
    data["prix_m2"] = data["valeur_fonciere"] / data["surface_reelle_bati"]
    return data

In [79]:
data = get_data()

In [80]:
data

date_mutation                     nature_mutation         nom_commune  \
0        2024-01-03                               Vente         Ludon-Médoc   
1        2024-01-08                               Vente             Canéjan   
2        2024-01-05                               Vente            Bordeaux   
3        2024-01-05                               Vente            Bordeaux   
4        2024-01-08                               Vente  Castelnau-de-Médoc   
...             ...                                 ...                 ...   
82597    2024-04-11                               Vente              Aillas   
82598    2024-04-11                               Vente              Aillas   
82599    2024-12-30  Vente en l'état futur d'achèvement            Le Teich   
82600    2024-12-30  Vente en l'état futur d'achèvement            Le Teich   
82601    2024-12-30  Vente en l'état futur d'achèvement            Le Teich   

       valeur_fonciere               adresse_nom_voie  surface_reelle_bati  \
0            336120.00           IMP DU PETIT FEYDIEU                 92.0   
1            400000.00                 CHE DE LEOGNAN                110.0   
2            175000.00           RUE PIERRE DE LADIME                  NaN   
3            175000.00                CRS DE LA SOMME                 53.0   
4            128000.00             RUE ANDRE MOULINAT                  NaN   
...                ...                            ...                  ...   
82597        183770.00              RTE DES GRAVIERES                  NaN   
82598        183770.00              RTE DES GRAVIERES                  NaN   
82599        210121.84  RUE EDOUARD ET JACQUES BEYNEL                  NaN   
82600        210121.84  RUE EDOUARD ET JACQUES BEYNEL                  NaN   
82601        210121.84                            NaN                  NaN   

                                     type_local  longitude   latitude  
0                                        Maison  -0.625239  44.974353  
1                                        Maison  -0.637939  44.747139  
2                                    Dépendance  -0.572046  44.816789  
3                                   Appartement  -0.572046  44.816789  
4                                           NaN  -0.814988  45.028059  
...                                         ...        ...        ...  
82597                                Dépendance  -0.051059  44.512979  
82598  Local industriel. commercial ou assimilé  -0.051059  44.512979  
82599                                       NaN  -1.024727  44.630550  
82600                                       NaN  -1.024727  44.630550  
82601                                       NaN  -1.024727  44.630550  

[82602 rows x 9 columns]

In [81]:
data = get_data_selected(data, nom_commune = "Bordeaux",
                      type_local = "Maison",
                      nature_mutation = "Vente")

In [82]:
def map_init(active=True):
    map_folium = folium.Map(
    prefer_canvas=True,
    min_zoom=10,
    max_zoom=15,
    location=(44.816789, -0.572046),
    zoom_control= False)
    return map_folium

In [83]:
map_folium = map_init()

In [84]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 958 entries, 102 to 82522
Data columns (total 10 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   date_mutation        958 non-null    object 
 1   nature_mutation      958 non-null    object 
 2   nom_commune          958 non-null    object 
 3   valeur_fonciere      958 non-null    float64
 4   adresse_nom_voie     958 non-null    object 
 5   surface_reelle_bati  958 non-null    float64
 6   type_local           958 non-null    object 
 7   longitude            958 non-null    float64
 8   latitude             958 non-null    float64
 9   prix_m2              958 non-null    float64
dtypes: float64(5), object(5)
memory usage: 82.3+ KB


In [89]:
def build_carto(data):
    for index, row in data.iterrows():
        lat = row["latitude"]
        long = row["longitude"]
    
        
        folium.CircleMarker([lat, long],
                    radius=5,
                    color="white",
                    weight=1,
                    popup=f"""
                      <div style=width:250px>
                      <p><b>{row['type_local']} - {row["adresse_nom_voie"]}</b></p>
                      <ul>
                                          
                         <li><b> Prix</b> : {row['valeur_fonciere']} | <b>Surface</b> : {int(row['surface_reelle_bati'])} m2</li>
                         
                         <li><b> Prix</b> : {int(row['prix_m2'])} € / m2</li>
    
                      </ul>
                      </div>
                    """,
                    fill_color="blue", # divvy color
                    ).add_to(map_folium)
    return map_folium

In [90]:
map_folium



In [ ]:
from es